## Initi

In [2]:
import easyocr
import cv2
import matplotlib.pyplot as plt
from icecream import ic
import os
import random
from moviepy.editor import VideoFileClip

In [3]:
def get_ocr_results(image_path):
    reader = easyocr.Reader(['en']) # this needs to run only once to load the model into memory
    result = reader.readtext(image_path)
    return result

In [4]:
def get_coordinates_for_text(data, target_text):
    matching_coordinates = []

    for item in data:
        coordinates, ocr_text, _ = item  # We ignore the confidence score here
        if target_text.lower() in ocr_text.lower() :  # Case-insensitive comparison
            matching_coordinates.append(coordinates)

    return matching_coordinates

In [5]:
def generate_video(input_video_path, output_video_path, top_left_coordinate, bottom_right_coordinate,band_color):
    """
    Draws a solid rectangle on a video with error handling.

    Parameters:
    - input_video_path: Path to the input video file.
    - output_video_path: Path where the output video will be saved.
    - top_left_coordinate: Tuple (x, y) for the top left coordinate of the rectangle.
    - bottom_right_coordinate: Tuple (x, y) for the bottom right coordinate of the rectangle.
    """
    try:
        # Attempt to open the input video
        cap = cv2.VideoCapture(input_video_path)
        if not cap.isOpened():
            raise IOError(f"Could not open video file: {input_video_path}")

        # Get the video properties
        frame_width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
        frame_height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
        fps = cap.get(cv2.CAP_PROP_FPS)

        # Generate output video path by appending '_output' before the file extension
        # base_name= os.path.basename(input_video_path)
        output_video_path = f"{output_video_path}.mp4"
        ic(output_video_path)

        # Define the codec and create a VideoWriter object
        out = cv2.VideoWriter(output_video_path, cv2.VideoWriter_fourcc(*'mp4v'), fps, (frame_width, frame_height))

        frame_count = 0  # To count the number of frames processed


        # Watermark
        text = "animated_home_solutions"
        font_scale=1
        alpha=0.5
        # Prepare text properties
        font = cv2.FONT_HERSHEY_SIMPLEX
        font_thickness = 2
        text_size = cv2.getTextSize(text, font, font_scale, font_thickness)[0]
        
        # Random initial position
        text_x = random.randint(0, frame_width - text_size[0])
        text_y = random.randint(0, frame_height - text_size[1])
        
        # Random direction
        direction_x = random.choice([-1, 1])
        direction_y = random.choice([-1, 1])
        step = 5  # Speed of the movement

        while True:
            ret, frame = cap.read()
            if not ret:
                break
            
            # Watermark
            
            # Create a transparent overlay for the watermark
            overlay = frame.copy()
            
            # Add text moving across the frame
            cv2.putText(overlay, text, (text_x, text_y), font, font_scale, (255, 255, 255), font_thickness)
            cv2.addWeighted(overlay, alpha, frame, 1 - alpha, 0, frame)
            
            # Update the position of the text for the next frame
            text_x += step * direction_x
            text_y += step * direction_y

            # Bounce off the edges
            if text_x + text_size[0] > frame_width or text_x < 0:
                direction_x *= -1
            if text_y + text_size[1] > frame_height or text_y < 0:
                direction_y *= -1
            
            # Watermark END

            # Draw a solid rectangle on the frame
            cv2.rectangle(frame, top_left_coordinate, bottom_right_coordinate, band_color, -1)

            # Add the text to the frame
            cv2.putText(frame, 'Follow for more', (top_left_coordinate[0]-10,top_left_coordinate[1]+25), font, font_scale, (255, 255, 255), 3)


            # Write the frame into the file
            out.write(frame)
            frame_count += 1
        
      
        print(f"Processed {frame_count} frames.")
    except IOError as e:
        print(f"IOError: {e}")
    except Exception as e:
        print(f"An unexpected error occurred: {e}")
    finally:
        # Release resources in the finally block to ensure they are always executed
        if 'cap' in locals() and cap.isOpened():
            cap.release()
        if 'out' in locals():
            out.release()
            

In [6]:
def add_audio(original_video_path, edited_video_path, output_video_path):
    """
    Adds the audio from the original video to the edited video.

    Parameters:
    - original_video_path: Path to the original video file.
    - edited_video_path: Path to the edited video file without audio.
    - output_video_path: Path where the output video with audio will be saved.
    """
    try:
        # Load the original and edited videos
        original_video = VideoFileClip(original_video_path)
        edited_video = VideoFileClip(edited_video_path)

        # Combine the audio from the original video with the edited video
        final_video = edited_video.set_audio(original_video.audio)

        # Write the output video file
        final_video.write_videofile(output_video_path, codec="libx264", audio_codec="aac")
        
        print(f"Successfully added audio to {output_video_path}")
    except Exception as e:
        print(f"Error adding audio to video: {e}")


In [7]:
def get_mid_frame(video_path,output_path = '',save_path=False):
    # Read the Video (Change the filename as per your file)
    cap = cv2.VideoCapture(video_path)

    # Get the total number of frames
    length = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    half_point = length//2 # Approximately half if number of frames are odd

    # Set the reader to the given frame number (half_point)
    cap.set(cv2.CAP_PROP_POS_FRAMES, half_point)

    # Read the frame
    ret, frame = cap.read()

    base_name = os.path.basename(video_path)
    print(base_name)
    if save_path: cv2.imwrite(f"{output_path}{base_name}_mid.png", frame)

    # Release the file pointer
    cap.release()
    return frame
# mid_frame = get_mid_frame(os.path.join('downloads','10_Parents Built a Beautiful Bedroom For Son & Daughter  3d Animation By The Stories Time  shorts.mp4'),output_path='',save_path=True)
# mid_frame = get_mid_frame('test.mp4',output_path='mid_frames/',save_path=True)
# mid_frame

### Actual code

In [8]:
mid_frame = get_mid_frame(r'test.mp4',output_path='mid_frames/',save_path=True)

test.mp4


In [9]:
ocr_results = get_ocr_results(mid_frame)
ocr_results

Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


[([[61, 55], [109, 55], [109, 69], [61, 69]], 'BEST', 0.9950381817750114),
 ([[28, 64], [136, 64], [136, 88], [28, 88]], 'INDIAN', 0.9313570263730901),
 ([[46, 86], [78, 86], [78, 94], [46, 94]], 'ILNE', 0.12265399098396301),
 ([[81, 83], [135, 83], [135, 97], [81, 97]], 'QAMINO', 0.46622896014818577),
 ([[47, 95], [119, 95], [119, 107], [47, 107]],
  'PLAIDEM',
  0.09117240543804958),
 ([[262, 1058], [462, 1058], [462, 1088], [262, 1088]],
  'The Stories Time',
  0.9996257111612783)]

In [10]:
matches = get_coordinates_for_text(ocr_results,'stories')
matches

[[[262, 1058], [462, 1058], [462, 1088], [262, 1088]]]

In [11]:
def get_mid_band_color(image,top_left):
    color = (image[top_left[1],top_left[0]])
    blue,green,red = int(color[0]),int(color[1]),int(color[2])
    ic(color)
    return blue,green,red

band_color = get_mid_band_color(mid_frame,[262, 1058])

ic| color: array([ 70,  80, 118], dtype=uint8)


In [12]:
top_left = matches[0][0]
ic(top_left)
bottom_right = matches[0][2]

top_left[1]-=15
bottom_right[1]+=15
ic(top_left)

ic| top_left: [262, 1058]


ic| top_left: [262, 1043]


[262, 1043]

In [13]:
generate_video('test.mp4','stage1/test_output',top_left_coordinate=top_left,bottom_right_coordinate=bottom_right,band_color = [ 70,  80, 118])

ic| output_video_path: 'stage1/test_output.mp4'


Processed 1318 frames.


## Loop

In [14]:
filenames = next(os.walk('downloads'), (None, None, []))[2]  

In [15]:
filenames_s = sorted(filenames, key=lambda x: int(x.split('_')[0]))

In [16]:
# for raw_name in list(reversed(filenames_s)):
#     v_name = raw_name.split('3d')[0].strip()+' 3D home redesign animations'+'_stage1'
#     filepath = os.path.join('downloads',raw_name)
#     ic(filepath)
#     ic(v_name)
#     mid_frame = get_mid_frame(filepath,output_path='mid_frames/',save_path=True)
#     ocr_results = get_ocr_results(mid_frame)
#     matches = get_coordinates_for_text(ocr_results,'stories')
#     top_left = matches[0][0]
#     bottom_right = matches[0][2]
#     band_color = get_mid_band_color(mid_frame,top_left)
#     # top_left[1]-=15
#     # bottom_right[1]+=15
#     generate_video(filepath,'stage1/'+v_name,top_left_coordinate=top_left,bottom_right_coordinate=bottom_right,band_color = band_color)
#     add_audio(filepath,'stage1/'+v_name+'.mp4','stage2/'+v_name+'.mp4')


In [17]:
import os
from concurrent.futures import ThreadPoolExecutor

def process_file(raw_name):
    v_name = raw_name.split('3d')[0].strip() + ' 3D home redesign animations' + '_stage1'
    filepath = os.path.join('downloads', raw_name)
    print(filepath)  # Assuming ic() was a placeholder for print or logging
    print(v_name)
    mid_frame = get_mid_frame(filepath, output_path='mid_frames/', save_path=True)
    ocr_results = get_ocr_results(mid_frame)
    matches = get_coordinates_for_text(ocr_results, 'stories')
    if matches:
        top_left, bottom_right = matches[0][0], matches[0][2]
        band_color = get_mid_band_color(mid_frame, top_left)
        generate_video(filepath, f'stage1/{v_name}', top_left_coordinate=top_left, bottom_right_coordinate=bottom_right, band_color=band_color)
        add_audio(filepath, f'stage1/{v_name}.mp4', f'stage3/{v_name}.mp4')

def main(filenames_s):
    with ThreadPoolExecutor() as executor:
        # Submit each file to be processed in a separate thread
        for raw_name in reversed(filenames_s):
            executor.submit(process_file, raw_name)

main(filenames_s)


downloads\74_Turn a Simple Room Into a Luxury Room in 3d Animation shorts.mp4
74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1
downloads\73_Husband Converted Simple Bedroom into Luxury Bedroom In 3d Animation shorts.mp4
73_Husband Converted Simple Bedroom into Luxury Bedroom In 3D home redesign animations_stage1
downloads\72_I Made Luxury & Perfect Bedroom For Son  3D Animation By The Stories Time  shorts.mp4
72_I Made Luxury & Perfect Bedroom For Son  3D Animation By The Stories Time  shorts.mp4 3D home redesign animations_stage1
downloads\71_I Made Luxury & Perfect Bedroom For Daughter  3d Animation By The Stories Time  shorts.mp4
71_I Made Luxury & Perfect Bedroom For Daughter 3D home redesign animations_stage1
downloads\70_I Made Luxury & Perfect Bedroom For Noughty Child  3d Animation By The Stories Time  shorts.mp4
70_I Made Luxury & Perfect Bedroom For Noughty Child 3D home redesign animations_stage1
downloads\69_Turn a Simple Living Room Into a Per

73_Husband Converted Simple Bedroom into Luxury Bedroom In 3d Animation shorts.mp4
71_I Made Luxury & Perfect Bedroom For Daughter  3d Animation By The Stories Time  shorts.mp4
74_Turn a Simple Room Into a Luxury Room in 3d Animation shorts.mp4
67_Made a Beautiful Bedroom for My   Daughter  3d Animation By The Stories Time  shorts.mp4
69_Turn a Simple Living Room Into a Perfect & Luxury Living Room in 3d Animation  shorts.mp4
70_I Made Luxury & Perfect Bedroom For Noughty Child  3d Animation By The Stories Time  shorts.mp4
65_I Made a Luxury & Perfect Bedroom For Two Son  3d Animation By The Stories Time  shorts.mp4
72_I Made Luxury & Perfect Bedroom For Son  3D Animation By The Stories Time  shorts.mp4
66_I Made Luxury & Perfect Study Room & Bedroom  3d Animation By The Stories Time  shorts.mp4
63_Made a Beautiful & Luxury Bedroom For My Son  3d Animation By The Stories Time  shorts.mp4
64_I Made a Luxury & Perfect Bathroom For Children  3d Animation By The Stories Time  shorts.mp4


Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster wi

68_I Made Luxury & Perfect Kitchen  3d Animation By The Stories Time  shorts.mp4


ic| color: array([ 72,  80, 116], dtype=icuint8|)
 color:icic |icarray|(|  [color output_video_path color::ic72ic:  ic|, array  |(80(|  array',[(  stage1/73_Husband Converted Simple Bedroom into Luxury Bedroom In 3D home  colorcolor[116'72 :]:72
color,,,                             :  dtypearray8080'array =,,redesign animations_stage1.mp4(uint8(array )'ic [116)[
(116 ]|
 [],72,  72  ,dtypedtype,color==72  icuint8  uint8:)80,)80|
  ,
 ,80ic  array116 ,icic|output_video_path116] (|],| :116 [,  ]color dtype  output_video_path,:=(output_video_pathdtype74: uint8 '=:dtype, ic)uint8arraystage1/65_I Made a Luxury & Perfect Bedroom For Two Son 3D home redesign =( 
  )(|uint8''82(
)[stage1/72_I Made Luxury & Perfect Bedroom For Son  3D Animation By The icic 

,''  ic|ic|color
                        74stage1/66_I Made Luxury & Perfect Study Room & Bedroom 3D home redesign 118| '|,'                         ic:]animations_stage1.mp4 output_video_path  '
,color  'colorStories Time  shorts.mp4 3D ho

...

Moviepy - video ready stage3/3_Parents Made a Attractive Bedroom For Twin Daughter 3D home redesign animations_stage1.mp4





t:  47%|████▋     | 776/1636 [01:45<00:15, 54.44it/s, now=None]

Successfully added audio to stage3/3_Parents Made a Attractive Bedroom For Twin Daughter 3D home redesign animations_stage1.mp4





t:  48%|████▊     | 780/1636 [01:45<00:18, 47.23it/s, now=None]


t:  48%|████▊     | 786/1636 [01:45<00:19, 43.44it/s, now=None]


t:  48%|████▊     | 791/1636 [01:46<00:24, 34.44it/s, now=None]


t:  49%|████▉     | 800/1636 [01:46<00:19, 42.38it/s, now=None]


t:  49%|████▉     | 807/1636 [01:46<00:17, 47.38it/s, now=None]


t:  50%|████▉     | 813/1636 [01:46<00:17, 48.08it/s, now=None]


t:  50%|█████     | 822/1636 [01:46<00:14, 57.01it/s, now=None]


t:  51%|█████     | 831/1636 [01:46<00:13, 57.61it/s, now=None]


t:  51%|█████▏    | 842/1636 [01:46<00:11, 70.03it/s, now=None]


t:  52%|█████▏    | 850/1636 [01:47<00:11, 66.03it/s, now=None]


t:  53%|█████▎    | 859/1636 [01:47<00:13, 57.23it/s, now=None]


t:  53%|█████▎    | 867/1636 [01:47<00:13, 58.95it/s, now=None]


t:  54%|█████▎    | 876/1636 [01:47<00:11, 64.20it/s, now=None]


t:  54%|█████▍    | 883/1636 [01:47<00:12, 60.52it/s, now=None]


t:  55%|█████▍    | 895/1636 [01:47<00:10, 69.25it/s, now=None]


t:  55%

Moviepy - Done !
Moviepy - video ready stage3/0_Parents Made a Perfect & Luxury Bedroom For Daughter 3D home redesign animations_stage1.mp4
Successfully added audio to stage3/0_Parents Made a Perfect & Luxury Bedroom For Daughter 3D home redesign animations_stage1.mp4
